Imports

In [48]:
from bs4 import BeautifulSoup as soup
from urllib.request import urlopen
import pandas as pd
import requests

Opening The Url

In [49]:
url = urlopen("http://www.northsouth.edu/")
nsu = soup(url.read())
#Examples of how to find by tag
#links = nsu.find_all('a')
#scripts = nsu.find_all('script')

Going through all the links

In [50]:
links = []

for link in nsu.find_all('a'):
  if 'href' in link.attrs:
    links.append((link.attrs['href']))

Creating dataframe for the links

In [51]:
links_df = pd.DataFrame(links)
links_df.head(2)

#Nameing the columns
links_df.columns = ['links']
links_df.head(2)


links
0  contact-us.html
1     archive.html

Modifying the dataframe

In [52]:
# Removing empty links from the dataframe
links_df = links_df[links_df["links"].str.contains("#") == False]
links_df.head(2)

links
0  contact-us.html
1     archive.html

In [53]:
# Removing external links from the data frame
internal_links = links_df[links_df["links"].str.contains("http") == False]
internal_links.head(2)

links
0  contact-us.html
1     archive.html

In [54]:
# Adding Https infront of all the addresses
internal_links['links'] = 'http://www.northsouth.edu/' + internal_links['links'].astype(str)
internal_links.head(2)

/var/folders/_w/kwxvx6js1gvfr3r6sz47fpmc0000gn/T/ipykernel_15923/3951678606.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  internal_links['links'] = 'http://www.northsouth.edu/' + internal_links['links'].astype(str)


links
0  http://www.northsouth.edu/contact-us.html
1     http://www.northsouth.edu/archive.html

In [55]:
# Creating new dataframe for external links
external_links = links_df[links_df["links"].str.contains("http") == True]
external_links.head(2)

links
5                      http://library.northsouth.edu
7  http://institutions.northsouth.edu/oea/interna...

Getting all the text data from the homepage

In [71]:
for data in nsu(['style', 'script', 'a', 'footer', 'nav']):
  # Remove tags
  data.decompose()

data = nsu.get_text()
data = data.replace("\n", " ")
#data = nsu.findAll('p')
data

'      Home | North South University                             NSU Ranked #1    In Bangladesh with the following international university ranking agencies      1. Times Higher Education (THE): 2023 (Public/Private Universities)  2. QS World University Ranking: 2022, 2021, 2020 (Private)    3. QS Asia University Ranking: 2023, 2022, 2021, 2020, 2019 (Private)    4. Webometrics University Ranking:   2022 (Private)                                                                                                                                                                Undergraduate Study                   Graduate Study                  Research                     Notice     27/03/2023      14/03/2023      13/03/2023      02/03/2023      23/02/2023                                       '

Creating a new list for all data of different website pages

In [72]:
website_data = pd.DataFrame({'address': ['http://www.northsouth.edu/'],
                             'title': ['Home | North South University'],
                             'data': [data]})
#website_data[data].replace("\n"," ")
website_data

address                          title  \
0  http://www.northsouth.edu/  Home | North South University   

                                                data  
0        Home | North South University           ...

Interlink and External Link seperated into their own list

In [58]:
internal_link_list = []
external_link_list = []

for item in links:
  if "http" in item:
    external_link_list.append(item)
  elif "#" in item:
    continue
  elif "pdf" in item:
    continue
  else:
    internal_link_list.append(item)


Adding full address to all internal links

In [59]:
internal_link_list_full = []
for item in internal_link_list:
  temp = "http://www.northsouth.edu/" + item
  internal_link_list_full.append(temp)

print(len(internal_link_list_full))
internal_link_list_full

95


['http://www.northsouth.edu/contact-us.html',
 'http://www.northsouth.edu/archive.html',
 'http://www.northsouth.edu/newsletter/nsu-catalog.html',
 'http://www.northsouth.edu/journals/',
 'http://www.northsouth.edu/newsletter.html',
 'http://www.northsouth.edu/academic/academic-calendar/',
 'http://www.northsouth.edu/about/brief-history.html',
 'http://www.northsouth.edu/about/vms.html',
 'http://www.northsouth.edu/about/int-ab.html',
 'http://www.northsouth.edu/about/accreditation.html',
 'http://www.northsouth.edu/about/international-recognition.html',
 'http://www.northsouth.edu/about/facts.html',
 'http://www.northsouth.edu/about/bot/',
 'http://www.northsouth.edu/academic/sbe/',
 'http://www.northsouth.edu/academic/sbe/acc-fin/',
 'http://www.northsouth.edu/academic/sbe/economics.html',
 'http://www.northsouth.edu/academic/sbe/mgt.html',
 'http://www.northsouth.edu/academic/sbe/mib.html',
 'http://www.northsouth.edu/academic/sbe/mba-emba/',
 'http://www.northsouth.edu/academic/sep

Getting All Links

In [60]:
def get_links_from_list(url_list, temp_url_list):
  for url in url_list:
    headers = {"User-Agent":"Mozilla/5.0"}
    response = requests.get(url, headers=headers)
    print("Accessing URL -------------------------- " + url)
    nsu_data = soup(response.text, 'lxml')
    for link in nsu_data.find_all('a'):
      if 'href' in link.attrs:
          temp = link.attrs['href']
          print("Url Found - " + temp)
          if "http" in temp:
            continue
          elif "#" in temp:
            continue
          elif "pdf" in temp:
              continue
          elif "//" in temp:
            continue
          elif "gmail" in temp:
            continue
          elif "mailto" in temp:
            continue
          elif "jpg" in temp:
            continue
          elif "jpeg" in temp:
            continue
          elif "png" in temp:
            continue
          elif "doc" in temp:
            continue
          elif "docx" in temp:
            continue
          elif "xls" in temp:
            continue
          elif "pptx" in temp:
            continue
          elif "~" in temp:
            continue
          elif "http://www.northsouth.edu/" + temp in temp_url_list:
            continue
          else:
            print("Appending Link ----- http://www.northsouth.edu/" +temp)
            temp_url_list.append("http://www.northsouth.edu/" + temp)
  print("def get links from list temp list size")
  print(len(temp_url_list))

In [61]:
# Getting links from the links in internal links list
temp_url_list_1 = []
temp_url_list_2 = []

print(len(temp_url_list_1))
print(len(temp_url_list_2))

get_links_from_list(internal_link_list_full, temp_url_list_1)
get_links_from_list(temp_url_list_1, temp_url_list_2)

0
0
Accessing URL -------------------------- http://www.northsouth.edu/contact-us.html
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Appending Link ----- http://www.northsouth.edu/academic/academic-calendar/
Url Found - newsletter.html
Appending Link ----- http://www.northsouth.edu/newsletter.html
Url Found - journals/
Appending Link ----- http://www.northsouth.edu/journals/
Url Found - newsletter/nsu-catalog.html
Appending Link ----- http://www.northsouth.edu/newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Appending Link ----- http://www.northsouth.edu/all-career-at-nsu/
Url Found - archive.html
Appending Link ----- http://www.northsouth.edu/archive.html
Url Found - contact-us.html
Appending Link ----- http://www.northsouth.edu/contact-us.html
Url Found - #
Url Found - http://www.

Accessing URL -------------------------- http://www.northsouth.edu/archive.html
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.pdf
Url Fou

Accessing URL -------------------------- http://www.northsouth.edu/newsletter/nsu-catalog.html
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndic

Accessing URL -------------------------- http://www.northsouth.edu/newsletter.html
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.pdf
Url 

Accessing URL -------------------------- http://www.northsouth.edu/academic/academic-calendar/
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndic

...

Accessing URL -------------------------- http://www.northsouth.edu/upcoming-events/?page=3
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.

Accessing URL -------------------------- http://www.northsouth.edu/upcoming-events/?page=4
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.

Accessing URL -------------------------- http://www.northsouth.edu/upcoming-events/?page=5
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.

Accessing URL -------------------------- http://www.northsouth.edu/upcoming-events/?page=6
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.

Accessing URL -------------------------- http://www.northsouth.edu/upcoming-events/?page=7
Url Found - https://rds3.northsouth.edu/index.php/nsuresearch
Url Found - http://institutions.northsouth.edu/oea/international-affairs/partnership/list-of-mous/
Url Found - academic/academic-calendar/
Url Found - newsletter.html
Url Found - journals/
Url Found - newsletter/nsu-catalog.html
Url Found - http://library.northsouth.edu
Url Found - all-career-at-nsu/
Url Found - archive.html
Url Found - contact-us.html
Url Found - #
Url Found - http://www.northsouth.edu/
Url Found - #
Url Found - about/brief-history.html
Url Found - about/vms.html
Url Found - about/int-ab.html
Url Found - about/accreditation.html
Url Found - about/international-recognition.html
Url Found - about/facts.html
Url Found - about/bot/
Url Found - about/executive-leaders.html#one
Url Found - about/executive-leaders.html#six
Url Found - about/executive-leaders.html#two
Url Found - http://www.northsouth.edu/assets/cv/Syndicate.

In [62]:
print(len(temp_url_list_1))
print(len(temp_url_list_2))

735
2005


In [63]:
print(temp_url_list_2)

['http://www.northsouth.edu/academic/academic-calendar/', 'http://www.northsouth.edu/newsletter.html', 'http://www.northsouth.edu/journals/', 'http://www.northsouth.edu/newsletter/nsu-catalog.html', 'http://www.northsouth.edu/all-career-at-nsu/', 'http://www.northsouth.edu/archive.html', 'http://www.northsouth.edu/contact-us.html', 'http://www.northsouth.edu/about/brief-history.html', 'http://www.northsouth.edu/about/vms.html', 'http://www.northsouth.edu/about/int-ab.html', 'http://www.northsouth.edu/about/accreditation.html', 'http://www.northsouth.edu/about/international-recognition.html', 'http://www.northsouth.edu/about/facts.html', 'http://www.northsouth.edu/about/bot/', 'http://www.northsouth.edu/academic/sbe/', 'http://www.northsouth.edu/academic/sbe/acc-fin/', 'http://www.northsouth.edu/academic/sbe/economics.html', 'http://www.northsouth.edu/academic/sbe/mgt.html', 'http://www.northsouth.edu/academic/sbe/mib.html', 'http://www.northsouth.edu/academic/sbe/mba-emba/', 'http://ww

In [64]:
temp_url_list_1

['http://www.northsouth.edu/academic/academic-calendar/',
 'http://www.northsouth.edu/newsletter.html',
 'http://www.northsouth.edu/journals/',
 'http://www.northsouth.edu/newsletter/nsu-catalog.html',
 'http://www.northsouth.edu/all-career-at-nsu/',
 'http://www.northsouth.edu/archive.html',
 'http://www.northsouth.edu/contact-us.html',
 'http://www.northsouth.edu/about/brief-history.html',
 'http://www.northsouth.edu/about/vms.html',
 'http://www.northsouth.edu/about/int-ab.html',
 'http://www.northsouth.edu/about/accreditation.html',
 'http://www.northsouth.edu/about/international-recognition.html',
 'http://www.northsouth.edu/about/facts.html',
 'http://www.northsouth.edu/about/bot/',
 'http://www.northsouth.edu/academic/sbe/',
 'http://www.northsouth.edu/academic/sbe/acc-fin/',
 'http://www.northsouth.edu/academic/sbe/economics.html',
 'http://www.northsouth.edu/academic/sbe/mgt.html',
 'http://www.northsouth.edu/academic/sbe/mib.html',
 'http://www.northsouth.edu/academic/sbe/mba

In [74]:
for tag in internal_link_list_full:
    headers = {"User-Agent":"Mozilla/5.0"}
    response = requests.get(tag, headers=headers)
    print("Accessing URL -------------------------- " + tag)
    data = soup(response.text, 'lxml')
    
    if data.find('title').string is None:
        continue
    
    title = data.find('title').string
    
    for item in data(['style', 'script', 'a', 'footer', 'nav', 'title']):
        # Remove tags
        item.decompose()
        
    print(title)
    
    temp_data = data.get_text()
    temp_data = temp_data.replace("\n", " ")
    #print(temp_data)
    
    temp_df = pd.DataFrame({'address': [tag],
                             'title': [title],
                             'data': [temp_data]})
        
    website_data = website_data.append({'address': tag, 'title': title, 'data': temp_data}, ignore_index=True)
    #website_data = website_data.append({'title': title}, ignore_index=True)
    #website_data = website_data.append({'data': temp_data}, ignore_index=True)
    
    

Accessing URL -------------------------- http://www.northsouth.edu/contact-us.html
Contact  | North South University
                               registrar@northsouth.edu  Location Map         


/var/folders/_w/kwxvx6js1gvfr3r6sz47fpmc0000gn/T/ipykernel_15923/760071918.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  website_data = website_data.append({'address': tag, 'title': title, 'data': temp_data}, ignore_index=True)


Accessing URL -------------------------- http://www.northsouth.edu/archive.html
Archive | North South University
                                                     Center of Excellence in Higher Education  The First Private University in Bangladesh            Archive           2023             2022                               2021                               2020                               2019                               2018                               2017                               2016                                      


/var/folders/_w/kwxvx6js1gvfr3r6sz47fpmc0000gn/T/ipykernel_15923/760071918.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  website_data = website_data.append({'address': tag, 'title': title, 'data': temp_data}, ignore_index=True)


Accessing URL -------------------------- http://www.northsouth.edu/newsletter/nsu-catalog.html
Catalogs | North South University
                                                     Center of Excellence in Higher Education  The First Private University in Bangladesh            Catalogs                    Year Action     2015-2016     2014-2015                


...

/var/folders/_w/kwxvx6js1gvfr3r6sz47fpmc0000gn/T/ipykernel_15923/760071918.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  website_data = website_data.append({'address': tag, 'title': title, 'data': temp_data}, ignore_index=True)


Accessing URL -------------------------- http://www.northsouth.edu/news-events/
News & Events | North South University
                                                     Center of Excellence in Higher Education  The First Private University in Bangladesh            News & Events             16/03/2023      16/03/2023      07/03/2023      26/02/2023      19/02/2023      06/02/2023      30/01/2023      30/01/2023      09/01/2023      26/12/2022      18/12/2022      21/11/2022      15/11/2022      31/10/2022      04/10/2022      25/09/2022      25/09/2022      25/08/2022      08/08/2022      26/07/2022                  


/var/folders/_w/kwxvx6js1gvfr3r6sz47fpmc0000gn/T/ipykernel_15923/760071918.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  website_data = website_data.append({'address': tag, 'title': title, 'data': temp_data}, ignore_index=True)


Accessing URL -------------------------- http://www.northsouth.edu/news-events/launchingceremony.html


AttributeError: 'NoneType' object has no attribute 'string'

In [75]:
website_data

address  \
0                          http://www.northsouth.edu/   
1           http://www.northsouth.edu/contact-us.html   
2              http://www.northsouth.edu/archive.html   
3   http://www.northsouth.edu/newsletter/nsu-catal...   
4                 http://www.northsouth.edu/journals/   
..                                                ...   
72       http://www.northsouth.edu/resources/fao.html   
73                     http://www.northsouth.edu/osa/   
74       http://www.northsouth.edu/registrars-office/   
75                    http://www.northsouth.edu/pshc/   
76             http://www.northsouth.edu/news-events/   

                                                title  \
0                       Home | North South University   
1                   Contact  | North South University   
2                    Archive | North South University   
3                   Catalogs | North South University   
4                   Journals | North South University   
..                                                ...   
72      Financial Aid Office | North South University   
73  Office of Student Affairs | North South Univer...   
74        Registrar's Office | North South University   
75       Complaint Committee | North South University   
76             News & Events | North South University   

                                                 data  
0         Home | North South University           ...  
1                                                 ...  
2                                                 ...  
3                                                 ...  
4                                                 ...  
..                                                ...  
72                                                ...  
73                                                ...  
74                                                ...  
75                                                ...  
76                                                ...  

[77 rows x 3 columns]